# TP3 & 4 - Artifical Intelligence

#### Marlon KUQI & Théo MARIE

### 1 - Recurrent neural network / LSTM : IMDB sentiment classification

![Encoders/Decoders for LTSM](https://qph.fs.quoracdn.net/main-qimg-febee5b881545802a75c064a84ecf85d)

In [9]:
'''
#Trains an LSTM model on the IMDB sentiment classification task.
The dataset is actually too small for LSTM to be of any advantage
compared to simpler, much faster methods such as TF-IDF + LogReg.
**Notes**
- RNNs are tricky. Choice of batch size is important,
choice of loss and optimizer is critical, etc.
Some configurations won't converge.
- LSTM loss decrease patterns during training can be quite different
from what you see with CNNs/MLPs/etc.
'''

from __future__ import print_function

from keras.datasets import imdb

from keras.layers import Dense, Embedding
from keras.layers import Dropout
from keras.layers import LSTM

from keras.models import Sequential

from keras.preprocessing import sequence

# load the dataset but only keep the first max_features words, zero the rest
max_features = 20000
maxlen = 80
batch_size = 32

# ---------- Data preparation -----------

# Loads data from the imdb dataset
print('Loading data...')
(x_train, y_train), (x_test, y_test) = imdb.load_data(num_words=max_features)
print(len(x_train), 'train sequences')
print(len(x_test), 'test sequences')

# Reshapes the training and testing sets
print('Pad sequences (samples x time)')
x_train = sequence.pad_sequences(x_train, maxlen=maxlen)
x_test = sequence.pad_sequences(x_test, maxlen=maxlen)
print('x_train shape:', x_train.shape)
print('x_test shape:', x_test.shape)

# ---------- Model building -----------

print('Build model...')
model = Sequential()

# The Embedding layer indicates that we work on a vocabulary (i.e. distinct words) of size "max_features"
# Our embedding vectors will have a size of 128
model.add(Embedding(max_features, 32))


# The LSTM layer will have an output size of 128 (128 memory units or smart neurons)
# "dropout" -> Fraction of the units to drop for the linear transformation of the inputs.
# "recurrent_dropout" -> Fraction of the units to drop for the linear transformation of the recurrent state.
model.add(LSTM(32, dropout=0.6, recurrent_dropout=0.2))


# The last layer of our NN will be a regular one, with a single neuron and activated by a sigmoid function 
# to make 0 or 1 predictions for the two classes (good and bad) in the problem.
model.add(Dense(1, activation='sigmoid'))

# Compiles the model
# "loss" -> Because it is a binary classification problem, log loss is used as the loss function
# "optimizer" -> Optimizer for the convergence of the loss function, here adam. We used SGD in the last TPs
# "metrics" -> List of metrics to be evaluated during testing and training
model.compile(loss='binary_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])

print('Train...')
# "batch_size" -> Here, weights are adjusted at each iteration
# "epochs" --> Fixed the number of iterations to 1000
model.fit(x_train, y_train,
          batch_size=batch_size,
          epochs=5,
          validation_data=(x_test, y_test))
#.evaluate(x, y, verbose) computes the loss
# x --> list of numpy arrays of test data
# y --> list of numpy arrays of target data
# batch_size -> Number of samples per gradient update. Weights are adjusted at each iteration
score, acc = model.evaluate(x_test, y_test,
                            batch_size=batch_size)
print('Test score:', score)
print('Test accuracy:', acc)

Loading data...
25000 train sequences
25000 test sequences
Pad sequences (samples x time)
x_train shape: (25000, 80)
x_test shape: (25000, 80)
Build model...
Train...
Train on 25000 samples, validate on 25000 samples
Epoch 1/5
25000/25000 [==============================] - 28s 1ms/step - loss: 0.5050 - acc: 0.7490 - val_loss: 0.3835 - val_acc: 0.8313
Epoch 2/5
25000/25000 [==============================] - 27s 1ms/step - loss: 0.3467 - acc: 0.8550 - val_loss: 0.3568 - val_acc: 0.8425
Epoch 3/5
25000/25000 [==============================] - 27s 1ms/step - loss: 0.2874 - acc: 0.8852 - val_loss: 0.4313 - val_acc: 0.8213
Epoch 4/5
25000/25000 [==============================] - 27s 1ms/step - loss: 0.2431 - acc: 0.9050 - val_loss: 0.3950 - val_acc: 0.8372
Epoch 5/5
25000/25000 [==============================] - 3s 118us/step
Test score: 0.4074541076183319
Test accuracy: 0.83516


#### Our first results give the following figures:

Test score: 1.1003549643659591

Test accuracy: 0.8094

### 2 - Text classification: the Ohsumed dataset

In [10]:
import numpy as np
import pandas as pd
import os
from collections import defaultdict

#### 1- Computing some statistics about the Ohsumed dataset

#### Number of files for each category

In [11]:
categories = 23

training_path = "ohsumed-first-20000\\training\C"
test_path = "ohsumed-first-20000\\test\C"

filecount = defaultdict(int)

for i in range(1,categories+1) :
    if (i < 10) :
        current_category = str("0" + str(i))
    else :
        current_category = str(i)
        
    for root, dirs, files in os.walk(training_path + current_category):  
        filecount[current_category] += len(files)
            
    for root, dirs, files in os.walk(test_path + current_category):  
        filecount[current_category] += len(files)

print("CAT  NB OF FILES")
print("----------------")
for key, value in filecount.items():
    print("C" + str(key) + "\t" + str(value))

CAT  NB OF FILES
----------------
C01	929
C02	391
C03	135
C04	2630
C05	712
C06	1220
C07	246
C08	1073
C09	254
C10	1562
C11	364
C12	1039
C13	667
C14	2550
C15	535
C16	428
C17	643
C18	788
C19	382
C20	1220
C21	1263
C22	183
C23	3952


#### Frequency of words in the C03 category

In [12]:
current_category = "03"

training_path = "ohsumed-first-20000\\training\C"
test_path = "ohsumed-first-20000\\test\C" 

wordcount = defaultdict(int)

for root, dirs, files in os.walk(training_path + current_category):  
    for filename in files:
        # print(filename)
        with open(training_path + current_category + "\\" + filename) as file:
            for word in file.read().split():
                wordcount[word] += 1

    for k,v in sorted(wordcount.items(), reverse=True, key=lambda x: x[1]):
        print (k, v) 

of 516
the 464
in 309
and 296
with 188
to 182
a 133
were 116
was 110
for 90
from 72
patients 67
by 65
is 58
The 54
or 52
that 41
as 36
at 35
infection 35
than 34
be 31
after 30
on 30
are 30
disease 27
not 27
In 27
an 26
A 26
this 25
cases 24
had 23
falciparum 22
treated 21
levels 21
treatment 20
cerebral 20
clinical 20
all 19
We 19
patient 18
these 18
malaria 18
no 17
2 17
Plasmodium 17
drug 16
isolates 16
1 15
diagnosis 15
but 15
parasite 15
antibody 15
only 15
study 15
studies 14
been 14
most 14
during 14
blood 14
rosetting 14
less 14
day 13
children 13
may 13
parasites 13
antibodies 13
leishmaniasis 13
days 13
other 13
3 12
between 12
disease. 12
transmission 12
antigens 12
against 12
acquired 12
infections 12
infected 12
associated 12
significantly 12
months 11
compared 11
there 11
lesions 11
found 11
present 11
pulmonary 11
Toxoplasma 11
control 11
peptides 11
response 11
sera 11
case 11
which 11
greater 11
C. 11
5 11
renal 11
positive 10
before 10
However, 10
have 10
infection. 1

detailed 2
fundus 2
pigment 2
edge 2
chorioretinal 2
progress 2
retina 2
retinochoroiditis 2
scan 2
nerve. 2
eye 2
brucellosis. 2
alert 2
central 2
nervous 2
parts 2
scoleces 2
report 2
rare 2
echinococcosis 2
Indians 2
Caribbean 2
standard 2
neurologic 2
seizures 2
primarily 2
electron 2
microscopy. 2
intractable 2
mapping 2
fine 2
specificity 2
molecule 2
IgE 2
positive) 2
anti-paramyosin 2
IgG2 2
IgG4 2
sexually 2
molluscum 2
contagiosum, 2
scabies, 2
crab 2
lice 2
itching 2
sections 2
reaction 2
allowed 2
lenses. 2
rinsed 2
stored 2
them 2
Scottish 2
forms 2
rosettes, 2
outcome 2
distribution. 2
status 2
mothers 2
permeability 2
PMA, 2
nonactivated 2
Kf,c 2
pressure 2
eosinophil 2
Endoscopic 1
cholangiopancreatography 1
clonorchiasis--a 1
Cholangiographic 1
biliary 1
clonorchiasis, 1
ova 1
isolates, 1
studied. 1
epigastric 1
(5 1
16) 1
fever 1
12.5% 1
(2 1
Praziquantel 1
administered. 1
87.5% 1
(14 1
ERCP 1
interval 1
31.6 1
(range, 1
69 1
months). 1
Measurements 1
retrograde 1
cho

Guinea. 1
Geographical 1
Uninfected 1
bind 1
spontaneous 1
rosetting. 1
75 1
fresh 1
Africa, 1
South 1
America, 1
Asia. 1
49% 1
tested; 1
(RBC) 1
0-75% 1
scored 1
73 1
(21%) 1
Liberian 1
disruption 1
dependent 1
RBC 1
Erythrocyte 1
geographically 1
phenomenon. 1
seem 1
rosette 1
formation 1
distinct 1
Studies 1
leading 1
monkey 1
safety, 1
immunogenicity, 1
protectivity. 1
minimal 1
FVO 1
strain, 1
vaccination 1
(S7 1
S12 1
S17) 1
induction 1
immunity 1
strains. 1
boosting 1
observed, 1
S7, 1
S12, 1
S17, 1
challenge. 1
excellent 1
choices 1
Immunization 1
blood-stage 1
antigens. 1
(35.1, 1
55.1, 1
83.1) 1
corresponding 1
portions 1
35 1
syntheic 1
incorporating 1
(SPf66) 1
Aotus 1
nancymai. 1
combinations 1
separate 1
sources 1
(Centers 1
Control 1
[CDC], 1
Atlanta, 1
GA 1
Colombia) 1
polymer. 1
CDC 1
peptides. 1
alone. 1
Following 1
parasitemias 1
10%. 1
inconsistency 1
contrasted 1
protected 1
Ultrasonographical 1
efficiency 1
ultrasonography 1
(US) 1
characterization 1
evaluated. 1


#### Frequency of words in all categories

In [14]:
categories = 23

training_path = "ohsumed-first-20000\\training\C"
test_path = "ohsumed-first-20000\\test\C" 

wordcount = defaultdict(int)

for i in range(1,categories+1) :
    if (i < 10) :
        current_category = "0"+str(i)
    else :
        current_category = str(i)
        
    for root, dirs, files in os.walk(training_path + current_category):  
        for filename in files:
            with open(training_path + current_category + "\\" + filename) as file:
                for word in file.read().split():
                    wordcount[word] += 1
    for root, dirs, files in os.walk(test_path + current_category):
        for filename in files:
            with open(test_path + current_category + "\\" + filename) as file:
                for word in file.read().split():
                    wordcount[word] += 1
sorted_dict = sorted(wordcount.items(), reverse=True, key=lambda x: x[1])

print("SUM : " + str(sum(wordcount.values())) + " words.")
i = 0
for k,v in sorted(wordcount.items(), reverse=True, key=lambda x: x[1]):
    i+=1
    print (str(i) + " - ", k, v) 

SUM : 4057563 words.
1 -  of 189228
2 -  the 159208
3 -  and 127102
4 -  in 113444
5 -  with 68449
6 -  to 65781
7 -  a 58539
8 -  was 42996
9 -  patients 39606
10 -  were 38504
11 -  for 33085
12 -  The 30703
13 -  is 23532
14 -  that 22592
15 -  or 22572
16 -  by 22547
17 -  than 19192
18 -  from 16789
19 -  be 15416
20 -  as 14706
21 -  had 14516
22 -  an 14326
23 -  on 13821
24 -  at 13762
25 -  not 12100
26 -  after 12063
27 -  are 11496
28 -  less 10475
29 -  In 10186
30 -  this 9850
31 -  +/- 9129
32 -  have 8582
33 -  A 8461
34 -  may 8164
35 -  = 7839
36 -  but 7535
37 -  treatment 7320
38 -  who 7259
39 -  We 7236
40 -  these 7210
41 -  during 7124
42 -  disease 6691
43 -  between 6357
44 -  no 6276
45 -  been 6175
46 -  clinical 6164
47 -  more 6130
48 -  associated 6061
49 -  two 5998
50 -  study 5871
51 -  patient 5784
52 -  group 5765
53 -  blood 5644
54 -  which 5598
55 -  one 5396
56 -  cell 5366
57 -  all 5317
58 -  This 5303
59 -  has 5290
60 -  normal 5290
61 -  sign

667 -  production 708
668 -  increasing 706
669 -  acquired 706
670 -  procedures 706
671 -  do 704
672 -  subjects. 702
673 -  head 702
674 -  available 700
675 -  CT 700
676 -  discussed. 698
677 -  out 698
678 -  hepatitis 697
679 -  operation 695
680 -  leukemia 695
681 -  types 694
682 -  investigated 694
683 -  22 691
684 -  minutes 691
685 -  site 690
686 -  presenting 690
687 -  remaining 689
688 -  hormone 689
689 -  episodes 688
690 -  testing 688
691 -  visual 688
692 -  interval 687
693 -  alcohol 687
694 -  series 686
695 -  range 681
696 -  monoclonal 680
697 -  family 680
698 -  drugs 679
699 -  controls. 678
700 -  resistance 677
701 -  information 677
702 -  characteristics 676
703 -  Because 673
704 -  persistent 672
705 -  current 672
706 -  especially 672
707 -  stimulation 671
708 -  mechanisms 670
709 -  occlusion 670
710 -  direct 668
711 -  cardiovascular 665
712 -  health 665
713 -  prolonged 665
714 -  hemorrhage 665
715 -  moderate 664
716 -  selected 664
717

1333 -  therefore 357
1334 -  studies. 357
1335 -  typical 356
1336 -  HPV 355
1337 -  transfusion 354
1338 -  disseminated 354
1339 -  below 354
1340 -  rectal 353
1341 -  randomly 353
1342 -  undergone 353
1343 -  susceptibility 353
1344 -  mucosa 353
1345 -  colonic 353
1346 -  performed. 352
1347 -  temporal 352
1348 -  applied 351
1349 -  Study 351
1350 -  observations 350
1351 -  analysis. 350
1352 -  rapidly 350
1353 -  segment 349
1354 -  system. 349
1355 -  records 349
1356 -  lipid 349
1357 -  pressure. 348
1358 -  diet 348
1359 -  creatinine 348
1360 -  nuclear 348
1361 -  hip 347
1362 -  10% 347
1363 -  intraoperative 347
1364 -  rise 347
1365 -  density 347
1366 -  transmission 346
1367 -  lymphocyte 346
1368 -  causing 346
1369 -  critical 346
1370 -  patients) 345
1371 -  line 345
1372 -  autoimmune 345
1373 -  mellitus 344
1374 -  electron 343
1375 -  upon 343
1376 -  drainage 343
1377 -  survey 343
1378 -  component 343
1379 -  thrombosis 343
1380 -  flap 343
1381 -  i

2166 -  59 211
2167 -  61 211
2168 -  0.0001). 211
2169 -  showing 211
2170 -  training 211
2171 -  75% 210
2172 -  recognition 210
2173 -  1989. 210
2174 -  atypical 210
2175 -  transesophageal 210
2176 -  unstable 210
2177 -  endometrial 210
2178 -  selection 209
2179 -  obstruction. 209
2180 -  medium 209
2181 -  Based 208
2182 -  lymphoid 208
2183 -  identified. 208
2184 -  Thus 208
2185 -  steroid 208
2186 -  arthritis. 208
2187 -  correlations 208
2188 -  National 208
2189 -  men, 208
2190 -  alive 208
2191 -  gas 208
2192 -  examination, 207
2193 -  antimicrobial 207
2194 -  equivalent 207
2195 -  around 207
2196 -  circulation 207
2197 -  hematologic 207
2198 -  preliminary 207
2199 -  1988 207
2200 -  prognosis. 207
2201 -  potassium 207
2202 -  unchanged 207
2203 -  acids 207
2204 -  IL-6 207
2205 -  cerebellar 207
2206 -  IgM 206
2207 -  corneal 206
2208 -  tended 206
2209 -  medial 206
2210 -  infarction, 206
2211 -  episode 205
2212 -  arteriovenous 205
2213 -  account 205

2999 -  strength 146
3000 -  employed 146
3001 -  artery, 146
3002 -  BP 146
3003 -  organism 145
3004 -  flow, 145
3005 -  (two 145
3006 -  deformity 145
3007 -  depletion 145
3008 -  height 145
3009 -  polyclonal 145
3010 -  problems. 145
3011 -  platelets 145
3012 -  Sixteen 145
3013 -  ulceration 145
3014 -  (the 145
3015 -  4) 145
3016 -  sign 145
3017 -  sulfate 145
3018 -  autosomal 145
3019 -  papillary 145
3020 -  shoulder 145
3021 -  aerobic 144
3022 -  (in 144
3023 -  changed 144
3024 -  lungs 144
3025 -  agents. 144
3026 -  76 144
3027 -  level, 144
3028 -  scale 144
3029 -  CF 144
3030 -  Thirty 144
3031 -  gross 144
3032 -  characterization 144
3033 -  fatigue 144
3034 -  us 144
3035 -  range, 144
3036 -  M 144
3037 -  estimates 144
3038 -  HLA 144
3039 -  moderately 144
3040 -  0.005). 144
3041 -  Epstein-Barr 144
3042 -  enlarged 144
3043 -  paraneoplastic 144
3044 -  malformations 144
3045 -  nifedipine 144
3046 -  breathing 144
3047 -  AV 144
3048 -  translocation 143

...

121813 -  .72 1
121814 -  .64. 1
121815 -  8,661 1
121816 -  "High 1
121817 -  Beyond" 1
121818 -  experts. 1
121819 -  (Cronbach's 1
121820 -  .89 1
121821 -  .95). 1
121822 -  .95. 1
121823 -  CRI's 1
121824 -  DIS/DSM-III 1
121825 -  (17-64) 1
121826 -  (4-16) 1
121827 -  Checklist). 1
121828 -  externalizing 1
121829 -  internalizing 1
121830 -  Nitinol 1
121831 -  gooseneck 1
121832 -  right-angle 1
121833 -  nickel-titanium 1
121834 -  (nitinol) 1
121835 -  mm); 1
121836 -  gold-plated 1
121837 -  tungsten 1
121838 -  coils. 1
121839 -  10-mm 1
121840 -  retrievals 1
121841 -  Tears 1
121842 -  menisci: 1
121843 -  Static 1
121844 -  torn, 1
121845 -  meniscal-free 1
121846 -  Skateboarding 1
121847 -  skateboarding 1
121848 -  19,182 1
121849 -  37,180 1
121850 -  Nontrivial 1
121851 -  Likely 1
121852 -  prohibition 1
121853 -  skateboards 1
121854 -  streets 1
121855 -  highways, 1
121856 -  gear. 1
121857 -  cohabiting, 1
121858 -  (chronic) 1
121859 -  Divorce 1
121860 -  de

122812 -  87.8 1
122813 -  91.0 1
122814 -  arterialization. 1
122815 -  [NE] 1
122816 -  [5-HT]), 1
122817 -  harvested. 1
122818 -  NE, 1
122819 -  [-log 1
122820 -  M]) 1
122821 -  unresponsive; 1
122822 -  Veno-arterial 1
122823 -  (15.6 1
122824 -  (103.0 1
122825 -  (80.3 1
122826 -  arterialization, 1
122827 -  PGI2. 1
122828 -  gauze 1
122829 -  swabs. 1
122830 -  (2.07% 1
122831 -  47.8 1
122832 -  (2.97% 1
122833 -  alginate, 1
122834 -  patella, 1
122835 -  (nonunion 1
122836 -  fracture) 1
122837 -  ligament-allograft 1
122838 -  allograft-prosthesis 1
122839 -  abandon 1
122840 -  tubercle. 1
122841 -  lags 1
122842 -  patella-patellar 1
122843 -  collagen-based 1
122844 -  non-collagenous 1
122845 -  epiphenomenon 1
122846 -  osteogenesis. 1
122847 -  biocompatibility, 1
122848 -  biomaterials 1
122849 -  Efficacies 1
122850 -  94.5% 1
122851 -  (87.1%). 1
122852 -  abrasion. 1
122853 -  abortus, 1
122854 -  xeroradiographic 1
122855 -  Coordination 1
122856 -  OB/GYN, 1


123812 -  overpredicted 1
123813 -  +2.3 1
123814 -  +1.2 1
123815 -  Myotubes 1
123816 -  kd) 1
123817 -  408-kd 1
123818 -  45-48 1
123819 -  (TMJPD) 1
123820 -  Eversole 1
123821 -  Machado, 1
123822 -  69), 1
123823 -  85), 1
123824 -  Checklist. 1
123825 -  pain-free, 1
123826 -  chronicity) 1
123827 -  Transsynaptic 1
123828 -  (pyknosis 1
123829 -  hyperchromatosis; 1
123830 -  'dark 1
123831 -  neurons') 1
123832 -  I-II. 1
123833 -  subconvulsive 1
123834 -  Dark 1
123835 -  predominance) 1
123836 -  I-II, 1
123837 -  strychnine-treated 1
123838 -  omitted. 1
123839 -  Filler 1
123840 -  maize. 1
123841 -  waxy 1
123842 -  (Wx) 1
123843 -  wx 1
123844 -  (wx-B, 1
123845 -  wx-B1, 1
123846 -  wx-B6, 1
123847 -  wx-C4) 1
123848 -  (Wx-W23). 1
123849 -  980 1
123850 -  (bp), 1
123851 -  (filler 1
123852 -  1-131 1
123853 -  bronze 1
123854 -  (bz-R) 1
123855 -  1;88(5):2035] 1
123856 -  (285-320 1
123857 -  254-nm 1
123858 -  G.C----A.T 1
123859 -  substitutions, 1
123860 -  nont

124812 -  (174.6 1
124813 -  myofibrillae. 1
124814 -  Clip 1
124815 -  Spherical 1
124816 -  ("collagenous 1
124817 -  spherulosis"). 1
124818 -  (epitheliosis) 1
124819 -  "collagenous 1
124820 -  spherulosis" 1
124821 -  spherule. 1
124822 -  Histopathologists 1
124823 -  Fluorometric 1
124824 -  3-(p-hydroxyphenyl) 1
124825 -  propionic 1
124826 -  (HPPA) 1
124827 -  (ChE) 1
124828 -  [Enzyme 1
124829 -  3.1.1.8] 1
124830 -  ChE, 1
124831 -  benzoylcholine, 1
124832 -  HPPA 1
124833 -  fluorogenic 1
124834 -  fluorometrically 1
124835 -  spectrophotometric 1
124836 -  found? 1
124837 -  impulsivity. 1
124838 -  steroids: 1
124839 -  21-year-old, 1
124840 -  workout. 1
124841 -  Pertinent 1
124842 -  Nandrolone 1
124843 -  (19-nor-testosterone) 1
124844 -  (Ile) 1
124845 -  metyrapone, 1
124846 -  (4.93 1
124847 -  9.86% 1
124848 -  205-930, 1
124849 -  adapt. 1
124850 -  anti-anoretic 1
124851 -  205-930 1
124852 -  anoretic 1
124853 -  anti-anorectic 1
124854 -  LY233053: 1
124855

125812 -  (ACTH), 1
125813 -  endorphins 1
125814 -  contraceptive. 1
125815 -  (BTB) 1
125816 -  1,259 1
125817 -  (OC, 1
125818 -  7-7-7) 1
125819 -  696 1
125820 -  24.9%, 1
125821 -  17.5%, 1
125822 -  7-7-7 1
125823 -  late-package 1
125824 -  midpackage 1
125825 -  BTB. 1
125826 -  week). 1
125827 -  (483 1
125828 -  0.047), 1
125829 -  condylar, 1
125830 -  Micromotion 1
125831 -  femurs 1
125832 -  climbing. 1
125833 -  components). 1
125834 -  loads; 1
125835 -  degenerated. 1
125836 -  ungrafted 1
125837 -  abolishment 1
125838 -  cyclicity 1
125839 -  hypoestrogenism. 1
125840 -  PMS. 1
125841 -  (CEE) 1
125842 -  16-25, 1
125843 -  1-25) 1
125844 -  16-25), 1
125845 -  Calendar 1
125846 -  Experiences. 1
125847 -  (GH)-releasing 1
125848 -  hormone-induced 1
125849 -  (GHRH)-induced 1
125850 -  (inNS; 1
125851 -  (ivGHRH; 1
125852 -  microgram/kg) 1
125853 -  (inGHRH; 1
125854 -  10.6-16.0 1
125855 -  [inNS 1
125856 -  (AUC; 1
125857 -  263.7 1
125858 -  0.03] 1
125859 -  (

#### 2- Preprocessing data

In [15]:
from termcolor import colored

def printInfo(string) :
    print(colored('[INFO] ', 'blue'), string)
    
def printDone(string) :
    print(colored('[DONE] ', 'green'), string)

#### Defining some functions for preprocess of the data

In [16]:
import os
import nltk
from nltk.tokenize import RegexpTokenizer
from nltk.corpus import stopwords
  
stopwords = set(stopwords.words('english')) 

""" Removes stopwords from a wordlist and returns it back """
def removeStopwords(wordlist, stopwords):
    return [w for w in wordlist if w not in stopwords]

#this tokenizer splits the strings using the regex given in argument
tokenizer = RegexpTokenizer(r'\w+')

""" Creates a word list from all files contained in a given directory """
def createWordList(directory):
    wordlist = list()
    for subdir, dirs, files in os.walk(directory):
        for file in files:
            fichier = open(os.path.join(subdir, file), 'r')
            wordlist.append(tokenizer.tokenize(fichier.read()))
    flat_wordlist = [item for sublist in wordlist for item in sublist]
    return [x.lower() for x in flat_wordlist]

""" Sort dict by descending value and creating tuples of type (freq, word) """
def sortFreqDictDesc(freqdict):
    d = [(freqdict[key], key) for key in freqdict]
    d.sort()
    d.reverse()
    return d

#### Preprocessing the data using the above functions

In [18]:
from functools import reduce

cwd = os.getcwd()
printInfo('Current working directory:' + cwd)

data_dir = cwd + "/ohsumed-first-20000/"
training_data_dir = cwd + "/ohsumed-first-20000/training/"
test_data_dir = cwd + "/ohsumed-first-20000/test/"
categories = os.listdir(training_data_dir)

printInfo('Creation of the global word list contained in all articles.')
global_word_list = createWordList(data_dir)

printInfo('Filtering stopwords from the list.')
global_word_list = removeStopwords(global_word_list, stopwords)

printInfo('Filtering words containing numbers.')
global_word_list = [item for item in global_word_list if item.isalpha()]

printInfo('Creating word frequency dictionnary')
global_word_freq = sortFreqDictDesc(reduce( lambda d, c: d.update([(c, d.get(c,0)+1)]) or d, global_word_list, {}))

printInfo('Creating ordered list of words according to frequency.')
ordered_word_list = list()
ordered_freq = list()

for (freq, word) in global_word_freq:
    ordered_word_list.append(word)
    ordered_freq.append(freq)

# printInfo(global_word_freq[0:10])
# printInfo(ordered_freq[0:10])
# printInfo(ordered_word_list[0:10])

printDone("Creating x_test & x_train datasets")

# Creation des frequences de mots de chaque classe bases sur la ordered_word_list
# pour x_train : dossier training_data_dir et pour x_test : dossier test_data_dir
# calculer la frequence des mots de chaques classes puis les ordonner de la meme
# maniere que la ordered_word_list
x_train = []
x_test = []

for category in categories:
    printInfo("Processing train category " + category + "...")
    temp = createWordList(training_data_dir + category)
    temp_dict = reduce( lambda d, c: d.update([(c, d.get(c,0)+1)]) or d, temp, {}) # Calcule le nombre d'occurence de chaque mots
    exec(category + "_train = [0]*len(ordered_word_list)") # Cree les listes C01_train, C02_train...
    for word in temp_dict:
        if word in ordered_word_list:
            exec(category + "_train[ordered_word_list.index(word)] = temp_dict[word]")
    printInfo("Processing test category " + category + "...")
    temp = createWordList(test_data_dir + category)
    temp_dict = reduce(lambda d, c: d.update([(c, d.get(c, 0) + 1)]) or d, temp, {}) # Calcule le nombre d'occurence de chaque mots
    exec(category + "_test = [0]*len(ordered_word_list)")  # Cree les listes C01_test, C02_test...
    for word in temp_dict:
        if word in ordered_word_list:
            exec(category + "_test[ordered_word_list.index(word)] = temp_dict[word]")

# Liste de 23 listes des len(ordered_word_list) frequences de chaques categories
for category in categories:
    exec("x_train.append(" + category + "_train)")
    exec("x_test.append(" + category + "_train)")

printDone("Creating y_test & y_train datasets")
# Liste des 23 listes correspondant a une category [0, 1, 0, ..., 0] pour la category C02
y_train = [[0 for x in range(23)] for x in range(23)]
for x in range(23):
    y_train[x][x] = 1

y_test = y_train

[INFO]  Current working directory:C:\Users\Marlon\Documents\ai\AI_TPs\TP3_4
[INFO]  Creation of the global word list contained in all articles.
[INFO]  Filtering stopwords from the list.
[INFO]  Filtering words containing numbers.
[INFO]  Creating word frequency dictionnary
[INFO]  Creating ordered list of words according to frequency.
[DONE]  Creating x_test & x_train datasets
[INFO]  Processing train category C01...
[INFO]  Processing test category C01...
[INFO]  Processing train category C02...
[INFO]  Processing test category C02...
[INFO]  Processing train category C03...
[INFO]  Processing test category C03...
[INFO]  Processing train category C04...
[INFO]  Processing test category C04...
[INFO]  Processing train category C05...
[INFO]  Processing test category C05...
[INFO]  Processing train category C06...
[INFO]  Processing test category C06...
[INFO]  Processing train category C07...
[INFO]  Processing test category C07...
[INFO]  Processing train category C08...
[INFO]  Pro

#### Building our Neural Network

In [38]:
from keras.preprocessing import sequence
from keras.models import Sequential
from keras.layers import Dense, Embedding, LSTM

import numpy as np

max_features = len(ordered_word_list)
# cut texts after this number of words (among top max_features most common words)
maxlen = 80
batch_size = 32

x_train = np.array(x_train)
x_test = np.array(x_test)
y_train = np.array(y_train)
y_test = np.array(y_test)

print(x_train.shape)

printInfo(str(len(x_train)) + ' train sequences')
printInfo(str(len(x_test)) + ' test sequences')

printInfo('Pad sequences (samples x time)')

x_train = sequence.pad_sequences(x_train, maxlen=maxlen)
x_test = sequence.pad_sequences(x_test, maxlen=maxlen)

printInfo('x_train shape:' + str(x_train.shape))
printInfo('x_test shape:' + str(x_test.shape))

printInfo('Building model...')

# Sequential model is a linear stack of layers (i.e. multi-layered neural network)
model = Sequential()

# The Embedding layer indicates that we work on a vocabulary (i.e. distinct words) of size "max_features"
# Our embedding vectors will have a size of 128
model.add(Embedding(max_features, 64))

model.add(Dropout(0.2))
# The LSTM layer will have an output size of 128 (128 memory units or smart neurons)
# "dropout" -> Fraction of the units to drop for the linear transformation of the inputs.
# "recurrent_dropout" -> Fraction of the units to drop for the linear transformation of the recurrent state.
model.add(LSTM(64, dropout=0.2, recurrent_dropout=0.2))
model.add(Dropout(0.2))

# The last layer of our NN will be a regular one, of size 23 and activated by a sigmoid function
model.add(Dense(23, activation='sigmoid'))

# Compiles the model
# "loss" -> Because it is a binary classification problem, log loss is used as the loss function
# "optimizer" -> Optimizer for the convergence of the loss function, here we use adam because it is the most efficient.
# "metrics" -> List of metrics to be evaluated during testing and training
model.compile(loss='binary_crossentropy',
              optimizer='adam',
              metrics=['accuracy'])

printInfo('Training model...')

# "batch_size" -> Here, weights are adjusted at each iteration
# "epochs" --> Fixed the number of iterations to 1000
model.fit(x_train, y_train,
          batch_size=batch_size,
          epochs=15,
          validation_data=(x_test, y_test))
#.evaluate(x, y, verbose) computes the loss
# x --> list of numpy arrays of test data
# y --> list of numpy arrays of target data
# batch_size -> Number of samples per gradient update. Weights are adjusted at each iteration
score, acc = model.evaluate(x_test, y_test,
                            batch_size=batch_size)

printDone('Test score: ' + str(score))
printDone('Test accuracy: ' + str(acc))


(23, 80)
[INFO]  23 train sequences
[INFO]  23 test sequences
[INFO]  Pad sequences (samples x time)
[INFO]  x_train shape:(23, 80)
[INFO]  x_test shape:(23, 80)
[INFO]  Building model...
[INFO]  Training model...
Train on 23 samples, validate on 23 samples
Epoch 1/15
23/23 [==============================] - 3s 150ms/step - loss: 0.6933 - acc: 0.4839 - val_loss: 0.6898 - val_acc: 0.5388
Epoch 2/15
23/23 [==============================] - 0s 3ms/step - loss: 0.6903 - acc: 0.5879 - val_loss: 0.6863 - val_acc: 0.7146
Epoch 3/15
23/23 [==============================] - 0s 2ms/step - loss: 0.6872 - acc: 0.6673 - val_loss: 0.6826 - val_acc: 0.8355
Epoch 4/15
23/23 [==============================] - 0s 2ms/step - loss: 0.6821 - acc: 0.7845 - val_loss: 0.6790 - val_acc: 0.8733
Epoch 5/15
23/23 [==============================] - 0s 3ms/step - loss: 0.6790 - acc: 0.8299 - val_loss: 0.6748 - val_acc: 0.8752
Epoch 6/15
23/23 [==============================] - 0s 3ms/step - loss: 0.6743 - acc: 0.85

Test score: 0.23249267041683197
Test accuracy: 0.9565218091011047